In [19]:
from langchain_community.document_loaders import TextLoader
from langchain_text_splitters import CharacterTextSplitter
from langchain_google_genai import GoogleGenerativeAIEmbeddings
from langchain_chroma import Chroma

In [20]:
from dotenv import load_dotenv

load_dotenv()

True

In [21]:
import pandas as pd

books = pd.read_csv("books_cleaned.csv")

In [22]:
books

Unnamed: 0      isbn10  \
0               0  0195153448   
1               2  0060973129   
2               3  0374157065   
3               4  0393045218   
4               5  0399135782   
...           ...         ...   
65268       90310  8172235224   
65269       90311  8173031010   
65270       90312  817992162X   
65271       90313  8185300534   
65272       90314  9027712050   

                                                   title  \
0                                    Classical Mythology   
1                                   Decision in Normandy   
2      Flu: The Story of the Great Influenza Pandemic...   
3                                 The Mummies of Urumchi   
4                                 The Kitchen God's Wife   
...                                                  ...   
65268                                  Mistaken Identity   
65269                                Journey to the East   
65270  The Monk Who Sold His Ferrari: A Fable About F...   
65271                                          I Am that   
65272                           The Berlin Phenomenology   

                                            authors               categories  \
0                                Mark P. O. Morford                  Fiction   
1                                      Carlo D'Este               Philosophy   
2                                  Gina Bari Kolata                  Fiction   
3                                   E. J. W. Barber                  Fiction   
4                                           Amy Tan              Biographers   
...                                             ...                      ...   
65268                              Nayantara Sahgal  Indic fiction (English)   
65269                                 Hermann Hesse        Adventure stories   
65270                                  Robin Sharma         Health & Fitness   
65271  Sri Nisargadatta Maharaj;Sudhakar S. Dikshit               Philosophy   
65272                 Georg Wilhelm Friedrich Hegel                  History   

                                               thumbnail  \
0      http://books.google.com/books/content?id=9XzpG...   
1      http://books.google.com/books/content?id=hYVW0...   
2      http://books.google.com/books/content?id=xDfxi...   
3      http://books.google.com/books/content?id=Vp1PE...   
4      https://books.google.com/books/content?id=s6IR...   
...                                                  ...   
65268  http://books.google.com/books/content?id=q-tKP...   
65269  http://books.google.com/books/content?id=rq6JP...   
65270  http://books.google.com/books/content?id=c_7mf...   
65271  http://books.google.com/books/content?id=Fv_JP...   
65272  http://books.google.com/books/content?id=Vy7Sk...   

                                             description  published_year  \
0      A chance meeting with an elderly beekeeper tur...            2002   
1      A modern-day classic. "Gift from the Sea is li...            1991   
2      Dimple's parents are from India and she's spen...            1999   
3      “Death is the midnight runner.” – Arab proverb...            1999   
4      In 1986 two young English scholars stumble upo...            1991   
...                                                  ...             ...   
65268  On A Train Journey Home To North India After L...            2003   
65269  This book tells the tale of a man who goes on ...            2002   
65270  Wisdom to Create a Life of Passion, Purpose, a...            2003   
65271  This collection of the timeless teachings of o...            1999   
65272  Since the three volume edition ofHegel's Philo...            1981   

       average_rating  ratings_count  \
0                4.00              5   
1                4.50              7   
2                3.50              9   
3                0.00              0   
4                4.00              3   
...               ...            ...   
65268         

In [23]:
books["tagged_description"]

0        0195153448 Classical Mythology Mark P. O. Morf...
1        0060973129 Decision in Normandy Carlo D'Este A...
2        0374157065 Flu: The Story of the Great Influen...
3        0393045218 The Mummies of Urumchi E. J. W. Bar...
4        0399135782 The Kitchen God's Wife Amy Tan In 1...
                               ...                        
65268    8172235224 Mistaken Identity Nayantara Sahgal ...
65269    8173031010 Journey to the East Hermann Hesse T...
65270    817992162X The Monk Who Sold His Ferrari: A Fa...
65271    8185300534 I Am that Sri Nisargadatta Maharaj;...
65272    9027712050 The Berlin Phenomenology Georg Wilh...
Name: tagged_description, Length: 65273, dtype: object

In [24]:
books["tagged_description"].to_csv("tagged_description.txt",
                                   sep = "\n",
                                   index = False,
                                   header = False)

In [25]:
raw_documents = TextLoader("tagged_description.txt", encoding="utf-8").load()
text_splitter = CharacterTextSplitter(chunk_size=0, chunk_overlap=0, separator="\n")
documents = text_splitter.split_documents(raw_documents)

Created a chunk of size 286, which is longer than the specified 0
Created a chunk of size 300, which is longer than the specified 0
Created a chunk of size 354, which is longer than the specified 0
Created a chunk of size 549, which is longer than the specified 0
Created a chunk of size 369, which is longer than the specified 0
Created a chunk of size 596, which is longer than the specified 0
Created a chunk of size 542, which is longer than the specified 0
Created a chunk of size 609, which is longer than the specified 0
Created a chunk of size 502, which is longer than the specified 0
Created a chunk of size 564, which is longer than the specified 0
Created a chunk of size 350, which is longer than the specified 0
Created a chunk of size 298, which is longer than the specified 0
Created a chunk of size 648, which is longer than the specified 0
Created a chunk of size 321, which is longer than the specified 0
Created a chunk of size 555, which is longer than the specified 0
Created a 

In [32]:
documents[0]

Document(metadata={'source': 'tagged_description.txt'}, page_content='0195153448 Classical Mythology Mark P. O. Morford A chance meeting with an elderly beekeeper turns into a pivotal, personal transformation when fifteen-year-old Mary Russell discovers that the beekeeper is the reclusive Sherlock Holmes, who soon takes on the role of mentor and teacher.')

In [33]:
import os
from dotenv import load_dotenv
load_dotenv()
embedding = GoogleGenerativeAIEmbeddings(
    model="models/embedding-001", 
    google_api_key=os.getenv("GOOGLE_API_KEY")  # assuming you loaded it from .env
)
db_books = Chroma.from_documents(documents, embedding=embedding, persist_directory="./chroma_db")

KeyboardInterrupt: 

In [36]:
query = "nature and environment"
docs = db_books.similarity_search(query, k = 10)
docs

[Document(id='b3c72cad-f9c2-483e-8fea-f032ddfbd4be', metadata={'source': 'tagged_description.txt'}, page_content='Creatures Small (Poems and Pictures) Dennis Saunders 023744772X Earth Works is the only comprehensive guide available to the best new and classic books about nature and the environment for adults and YAs. It provides descriptive entries for trade nonfiction and scholarly or technical books, and a significant number of fiction titles which are of interest to both the general public and specialists. Each chapter defines its scope, then identifies key books or authors, and refers to notable related works in other chapters.'),
 Document(id='f81dc72c-2bd5-4062-a755-3640a031af72', metadata={'source': 'tagged_description.txt'}, page_content='023744772X Creatures Small (Poems and Pictures) Dennis Saunders Earth Works is the only comprehensive guide available to the best new and classic books about nature and the environment for adults and YAs. It provides descriptive entries for tr

In [39]:
import re
matching_book = books[
    books["isbn10"].astype(str)
         .eq(re.search(r"\b\d{9}[0-9X]\b", docs[0].page_content).group(0))
]
print(matching_book[["title", "authors", "isbn10"]])


                                      title          authors      isbn10
11136  Creatures Small (Poems and Pictures)  Dennis Saunders  023744772X


In [48]:
def retrieve_semantic_recommendations(
    query: str,
    top_k: int = 15,
) -> pd.DataFrame:
    # 1) over-fetch to avoid duplicates
    recs = db_books.similarity_search(query, k=top_k * 3)

    # 2) collect unique, existing ISBN10 tokens in order
    seen = set()
    unique_tokens = []
    # ensure our CSV isbn10s are strings
    valid_isbns = set(books["isbn10"].astype(str).tolist())

    for doc in recs:
        m = ISBN10_RE.search(doc.page_content or "")
        if not m:
            continue
        tok = m.group(0)
        # only keep new tokens that actually exist in your CSV
        if tok not in seen and tok in valid_isbns:
            seen.add(tok)
            unique_tokens.append(tok)
        if len(unique_tokens) >= top_k:
            break

    # 3) If you didn’t find enough, you’ll just return however many you did find
    if not unique_tokens:
        return pd.DataFrame(columns=books.columns)

    # 4) Build a DataFrame indexed by isbn10_str, then reindex to force order
    df = books.copy()
    df["isbn10_str"] = df["isbn10"].astype(str)
    df = df.set_index("isbn10_str")

    # reindex will create rows exactly in the order of unique_tokens
    result = (
        df.reindex(unique_tokens)        
          .reset_index(drop=True)
          .loc[:, books.columns]        # drop the helper column
    )

    return result

In [52]:
retrieve_semantic_recommendations("a cursed boy who goes to wizard school", top_k=10)

Unnamed: 0      isbn10                                              title  \
0       26824  081671827X        School of Wizardry (Circle of Magic Series)   
1       11866  3551551677              Harry Potter und der Stein der Weisen   
2        9786  0807281956  Harry Potter and the Sorcerer's Stone (Book 1 ...   
3       86902  0439554934     Harry Potter and the Sorcerer's Stone (Book 1)   
4       46273  2070541274  Harry Potter, tome 1 : Harry Potter Ã?Â  l'Ã?Â...   
5       80477  0939173344              Harry Potter and the Sorcerer's Stone   
6       47148  0345376021  My Son the Wizard (Stasheff, Christopher. Wiza...   
7       46271  2070541290  Harry Potter, tome 2 : Harry Potter et la Cham...   
8       84283  034547046X                 Negima: Magister Negi Magi, Vol. 1   
9       72862  1594130000              Harry Potter and the Sorcerer's Stone   

                authors                  categories  \
0           Debra Doyle            Juvenile Fiction   
1     Joanne K. Rowling            Juvenile Fiction   
2         J. K. Rowling                     Fiction   
3         Rowling, J.K.            Juvenile Fiction   
4     Joanne K. Rowling                     England   
5          J.K. Rowling  Braille books for children   
6  Christopher Stasheff            American fiction   
7     Joanne K. Rowling            Boarding schools   
8          KEN AKAMATSU     Comics & Graphic Novels   
9         J. K. Rowling            Juvenile Fiction   

                                           thumbnail  \
0  https://books.google.com/books/content?id=QnAw...   
1  https://books.google.com/books/content?id=XvAp...   
2  http://images.amazon.com/images/P/0807281956.0...   
3  http://books.google.com/books/content?id=9jA0B...   
4  https://books.google.com/books/content?id=57i3...   
5  http://images.amazon.com/images/P/0939173344.0...   
6  https://books.google.com/books/content?id=SHEM...   
7  https://books.google.com/books/content?id=w4AU...   
8  http://images.amazon.com/images/P/034547046X.0...   
9  https://books.google.com/books/content?id=j2eP...   

                                         description  published_year  \
0  Determined to become a wizard, twelve-year-old...            1990   
1  Eigentlich hatte Harry geglaubt, er sei ein ga...            1999   
2  Rescued from the outrageous neglect of his aun...            1999   
3  In Harry Potter and the Sorcerer's Stone, Harr...            2015   
4  Le jour de ses onze ans, Harry Potter, un orph...            1999   
5  Rescued from the outrageous neglect of his aun...            1999   
6  A WORLD OF TROUBLES--TIMES TWO! Matt Mantrell-...            1997   
7  Harry Potter fait une rentrée fracassante en v...            1999   
8  When ten-year-old wizard Negi Springfield rece...            2004   
9  Rescued from the outrageous neglect of his aun...            2003   

   average_rating  ratings_count  \
0            0.00              0   
1            5.00              1   
2            0.00              0   
3            4.47        5629932   
4            4.50              6   
5            0.00              0   
6            5.00              1   
7            5.00              1   
8            0.00              0   
9            0.00              0   

                                  tagged_description  
0  081671827X School of Wizardry (Circle of Magic...  
1  3551551677 Harry Potter und der Stein der Weis...  
2  0807281956 Harry Potter and the Sorcerer's Sto...  
3  0439554934 Harry Potter and the Sorcerer's Sto...  
4  2070541274 Harry Potter, tome 1 : Harry Potter...  
5  0939173344 Harry Potter and the Sorcerer's Sto...  
6  0345376021 My Son the Wizard (Stasheff, Christ...  
7  2070541290 Harry Potter, tome 2 : Harry Potter...  
8  034547046X Negima: Magister Negi Magi, Vol. 1 ...  
9  1594130000 Harry Potter and the Sorcerer's Sto...

In [54]:
import os
from pathlib import Path

import pandas as pd
from dotenv import load_dotenv
from langchain.text_splitter import CharacterTextSplitter
from langchain.schema import Document
from langchain.vectorstores import Chroma
from langchain_google_genai import GoogleGenerativeAIEmbeddings

# 1) Load environment variables
load_dotenv()
API_KEY = os.getenv("GOOGLE_API_KEY")
if not API_KEY:
    raise RuntimeError("Please set GOOGLE_API_KEY in your .env")

# 2) Paths

CSV_PATH ="./books_cleaned.csv"
DB_PATH  ="./chroma_db"

# 3) Read your CSV
books = pd.read_csv(CSV_PATH)
# ensure isbn10 is a string
books["isbn10"] = books["isbn10"].astype(str)

# 4) Prepare text splitter
splitter = CharacterTextSplitter(
    chunk_size=500,     # adjust as needed
    chunk_overlap=50,
    separator="\n"
)

# 5) Build Document list with metadata
documents = []
for _, row in books.iterrows():
    text = row["tagged_description"]
    # split into manageable chunks
    for chunk in splitter.split_text(text):
        documents.append(
            Document(
                page_content=chunk,
                metadata={"isbn10": row["isbn10"]}
            )
        )

# 6) Initialize embeddings and vector store
embeddings = GoogleGenerativeAIEmbeddings(
    model="models/embedding-001",
    google_api_key=API_KEY
)
db = Chroma.from_documents(
    documents=documents,
    embedding=embeddings,
    persist_directory=str(DB_PATH),
    collection_name="books"   # optional name
)

# 7) Persist to disk and report
db.persist()
vector_count = db._collection.count()
print(f"✅ Persisted {vector_count} vectors to {DB_PATH}")


✅ Persisted 65273 vectors to ./chroma_db


C:\Users\anupa\AppData\Local\Temp\ipykernel_14512\1358955693.py:60: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  db.persist()


In [4]:
import pandas as pd

df=pd.read_csv("../books/books_cleaned.csv")
df.head()


isbn13      isbn10                title  \
0  9780002005883  0002005883               Gilead   
1  9780002261982  0002261987         Spider's Web   
2  9780006178736  0006178731       Rage of angels   
3  9780006280897  0006280897       The Four Loves   
4  9780006280934  0006280935  The Problem of Pain   

                           authors                     categories  \
0               Marilynne Robinson                        Fiction   
1  Charles Osborne;Agatha Christie  Detective and mystery stories   
2                   Sidney Sheldon                        Fiction   
3              Clive Staples Lewis                 Christian life   
4              Clive Staples Lewis                 Christian life   

                                           thumbnail  \
0  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...   
1  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...   
2  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...   
3  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...   
4  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...   

                                         description  published_year  \
0  A NOVEL THAT READERS and critics have been eag...          2004.0   
1  A new 'Christie for Christmas' -- a full-lengt...          2000.0   
2  A memorable, mesmerizing heroine Jennifer -- b...          1993.0   
3  Lewis' work on the nature of love divides love...          2002.0   
4  "In The Problem of Pain, C.S. Lewis, one of th...          2002.0   

   average_rating  num_pages  ratings_count     title_and_subtitle  \
0            3.85      247.0          361.0                 Gilead   
1            3.83      241.0         5164.0  Spider's Web: A Novel   
2            3.93      512.0        29532.0         Rage of angels   
3            4.15      170.0        33684.0         The Four Loves   
4            4.09      176.0        37569.0    The Problem of Pain   

                                  tagged_description  
0  9780002005883 A NOVEL THAT READERS and critics...  
1  9780002261982 A new 'Christie for Christmas' -...  
2  9780006178736 A memorable, mesmerizing heroine...  
3  9780006280897 Lewis' work on the nature of lov...  
4  9780006280934 "In The Problem of Pain, C.S. Le...

In [56]:
import pandas as pd
import urllib.parse
import re

df = pd.read_csv("./books_cleaned.csv")

# compile once
GB_PATTERN = re.compile(r"^https?://books\.google\.com/books/content\?")

def proxify_if_google(thumbnail: str) -> str:
    # leave blank or non‑strings alone
    if not isinstance(thumbnail, str) or not thumbnail.strip():
        return thumbnail

    # only target the Google Books content URLs
    if not GB_PATTERN.match(thumbnail):
        return thumbnail

    # switch to https
    secure = thumbnail.replace("http:", "https:")
    # percent‑encode the whole thing
    encoded = urllib.parse.quote(secure, safe="")
    # proxy it
    return f"https://corsproxy.io/?{encoded}"

# apply only to the matching rows
df["thumbnail"] = df["thumbnail"].apply(proxify_if_google)

# inspect
print(df.loc[df["thumbnail"].str.contains("corsproxy", na=False), ["isbn10","thumbnail"]].head())

# save
df.to_csv("./books_cleaned.csv", index=False)


       isbn10                                          thumbnail
0  0195153448  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...
1  0060973129  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...
2  0374157065  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...
3  0393045218  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...
4  0399135782  https://corsproxy.io/?https%3A%2F%2Fbooks.goog...
